<a href="https://colab.research.google.com/github/yh08037/ABR-Lab-Summer-Project/blob/master/DogBreed_with_Generator_InceptionV3.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

# Dog Breed Classification

## Set Tensorflow 2.0

In [0]:
from __future__ import absolute_import, division, print_function, unicode_literals

try:
  # %tensorflow_version only exists in Colab.
  %tensorflow_version 2.x
except Exception:
    pass
import tensorflow as tf

TensorFlow 2.x selected.


## Download and inspect dataset

In [0]:
# 구글드라이브 파일 읽기 위한 연동 용 라이브러리
!pip install -U -q PyDrive

from pydrive.auth import GoogleAuth
from pydrive.drive import GoogleDrive
from google.colab import auth
from oauth2client.client import GoogleCredentials 


# 1. Authenticate and create the PyDrive client.

auth.authenticate_user()
gauth = GoogleAuth()
gauth.credentials = GoogleCredentials.get_application_default()
drive = GoogleDrive(gauth)

     |████████████████████████████████| 993kB 2.8MB/s 


train.zip : https://drive.google.com/open?id=1squZt709J4AEdrADfOrHEuBRc8GWFeI-

valid.zip : https://drive.google.com/open?id=1caXSPr2RKOopOoS2FevrC6qJc3AEMAe9

test.zip : https://drive.google.com/open?id=1j4gbulbo60cKxW2OXSDIaHrUUZV9RiXY

In [0]:
# 실질적으로 구글드라이브에서 파일을 불러오는 방법입니다.
# 위에서 준비해두었던 공유 가능한 링크에서 'id=' 이후에 있는 문자열을 복사하여 file_id로 사용합니다.
train_id = '1squZt709J4AEdrADfOrHEuBRc8GWFeI-'
valid_id = '1caXSPr2RKOopOoS2FevrC6qJc3AEMAe9'
test_id = '1j4gbulbo60cKxW2OXSDIaHrUUZV9RiXY'

downloaded = drive.CreateFile({'id': train_id})  # file_id로부터 파일 객체를 생성
downloaded.GetContentFile('train.zip')           # 불러온 파일 객체를 Colab에 저장

downloaded = drive.CreateFile({'id': valid_id})  
downloaded.GetContentFile('valid.zip')          

downloaded = drive.CreateFile({'id': test_id}) 
downloaded.GetContentFile('test.zip')         

# 압축해제
!unzip train.zip
!unzip valid.zip
!unzip test.zip

Archive:  train.zip
   creating: train/
   creating: train/n02098413-Lhasa/
  inflating: train/n02098413-Lhasa/n02098413_2911.jpg  
  inflating: train/n02098413-Lhasa/n02098413_11467.jpg  
  inflating: train/n02098413-Lhasa/n02098413_2954.jpg  
  inflating: train/n02098413-Lhasa/n02098413_13083.jpg  
  inflating: train/n02098413-Lhasa/n02098413_1457.jpg  
  inflating: train/n02098413-Lhasa/n02098413_624.jpg  
  inflating: train/n02098413-Lhasa/n02098413_3411.jpg  
  inflating: train/n02098413-Lhasa/n02098413_10144.jpg  
  inflating: train/n02098413-Lhasa/n02098413_8297.jpg  
  inflating: train/n02098413-Lhasa/n02098413_1473.jpg  
  inflating: train/n02098413-Lhasa/n02098413_2047.jpg  
  inflating: train/n02098413-Lhasa/n02098413_10285.jpg  
  inflating: train/n02098413-Lhasa/n02098413_2607.jpg  
  inflating: train/n02098413-Lhasa/n02098413_3285.jpg  
  inflating: train/n02098413-Lhasa/n02098413_3899.jpg  
  inflating: train/n02098413-Lhasa/n02098413_1655.jpg  
  inflating: train/n02098

## Set data generators

In [0]:
from tensorflow.keras.preprocessing.image import ImageDataGenerator

train_datagen = ImageDataGenerator(
    rescale=1./255,
    featurewise_center=True,
    featurewise_std_normalization=True,
    rotation_range=20,
    width_shift_range=0.2,
    height_shift_range=0.2,
    horizontal_flip=True)
valid_datagen = ImageDataGenerator(rescale=1./255)
test_datagen = ImageDataGenerator(rescale=1./255)

BATCH_SIZE = 32

train_datagen = train_datagen.flow_from_directory(
    directory='/content/train',
    target_size=(224, 224),
    batch_size=BATCH_SIZE)

valid_datagen = valid_datagen.flow_from_directory(
    directory='/content/valid',
    target_size=(224, 224),
    batch_size=BATCH_SIZE)

test_datagen = test_datagen.flow_from_directory(
    directory='/content/test',
    target_size=(224, 224),
    batch_size=BATCH_SIZE)

Found 18658 images belonging to 120 classes.
Found 961 images belonging to 120 classes.
Found 961 images belonging to 120 classes.


## Load and Define a model

In [0]:
from tensorflow import keras
from tensorflow.keras import layers

model = keras.applications.InceptionV3(
    input_shape=(224, 224, 3),
    include_top=False,
    pooling='avg',
    weights='imagenet')
model.trainable = False
output = keras.layers.Dense(120, 'softmax')(model.layers[-1].output)
logits = keras.layers.Dropout(0.5)(output)
model = keras.models.Model(model.inputs, logits)
model.compile('adam', 'categorical_crossentropy', ['accuracy'])

model.summary()

87916544/87910968 [==============================] - 7s 0us/step
Model: "model_1"
__________________________________________________________________________________________________
Layer (type)                    Output Shape         Param #     Connected to                     
input_2 (InputLayer)            [(None, 224, 224, 3) 0                                            
__________________________________________________________________________________________________
conv2d (Conv2D)                 (None, 111, 111, 32) 864         input_2[0][0]                    
__________________________________________________________________________________________________
batch_normalization (BatchNorma (None, 111, 111, 32) 96          conv2d[0][0]                     
__________________________________________________________________________________________________
activation (Activation)         (None, 111, 111, 32) 0           batch_normalization[0][0]        
___________________________

In [0]:
len(model.trainable_variables)

2

In [0]:
keras.utils.plot_model(model, 'Inception.png', show_shapes=True)

## Train the model with validation

In [0]:
STEP_SIZE_TRAIN = train_datagen.n // train_datagen.batch_size
STEP_SIZE_VALID = valid_datagen.n // valid_datagen.batch_size

In [15]:
model.fit_generator(generator=train_datagen, 
                    steps_per_epoch=STEP_SIZE_TRAIN, 
                    validation_data = valid_datagen,
                    validation_steps = STEP_SIZE_VALID,
                    epochs=10)

Epoch 1/10


/tensorflow-2.0.0-rc0/python3.6/keras_preprocessing/image/image_data_generator.py:716: UserWarning: This ImageDataGenerator specifies `featurewise_center`, but it hasn't been fit on any training data. Fit it first by calling `.fit(numpy_data)`.
  warnings.warn('This ImageDataGenerator specifies '
/tensorflow-2.0.0-rc0/python3.6/keras_preprocessing/image/image_data_generator.py:724: UserWarning: This ImageDataGenerator specifies `featurewise_std_normalization`, but it hasn't been fit on any training data. Fit it first by calling `.fit(numpy_data)`.
  warnings.warn('This ImageDataGenerator specifies '


583/583 [==============================] - 418s 717ms/step - loss: 9.1147 - accuracy: 0.2438 - val_loss: 0.8084 - val_accuracy: 0.7833
Epoch 2/10
583/583 [==============================] - 416s 713ms/step - loss: 8.6834 - accuracy: 0.3174 - val_loss: 0.7669 - val_accuracy: 0.8135
Epoch 3/10
583/583 [==============================] - 421s 722ms/step - loss: 8.5202 - accuracy: 0.3327 - val_loss: 0.8957 - val_accuracy: 0.8125
Epoch 4/10
583/583 [==============================] - 421s 722ms/step - loss: 8.6007 - accuracy: 0.3353 - val_loss: 0.8961 - val_accuracy: 0.7990
Epoch 5/10
583/583 [==============================] - 415s 711ms/step - loss: 8.6378 - accuracy: 0.3386 - val_loss: 0.9016 - val_accuracy: 0.8010
Epoch 6/10
583/583 [==============================] - 415s 711ms/step - loss: 8.6288 - accuracy: 0.3396 - val_loss: 0.8523 - val_accuracy: 0.8219
Epoch 7/10
583/583 [==============================] - 419s 719ms/step - loss: 8.6422 - accuracy: 0.3447 - val_loss: 0.9356 - val_accura

In [0]:
test_loss, test_acc = model.evaluate_generator(generator=test_datagen)

In [19]:
print('test accuracy :', test_acc)

test accuracy : 0.81789804
